In [41]:
# Jeffrey Chen 3035725536
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FFMpegWriter
import random
import datetime

%config InlineBackend.figure_format = 'retina'
%matplotlib osx

# define constants
width = 19
height = 28
GRAY = [150, 150, 150]
BALL_COLOR = [255, 0, 0]
WHITE = [255, 255, 255]
GREEN = [0, 255, 0]
BLACK = [0, 0, 0]
BALL_START_ROW = 1
FRAME_PAUSE = 0.25

In [42]:
def setup_board(height, width):
    # setup the regular board, initialize to all white
    board = 255 * np.ones([height,width,3],dtype='uint8')

    # fill in board
    for col in range(width):
        for row in range(height):
            # mark boundaries of board as black
            if row == 0 or row == height - 1 or col == 0 or col == width - 1:
                board[row][col] = BLACK

            # row == 1: starting area
            elif row == BALL_START_ROW:
                board[row][col] = GREEN
                
            # create end pegs, where the prizes would be
            elif row >= height - 3 and col % 2 == 0:
                board[row][col] = GRAY

    # setup obstacle pegs, using counter to alternate the positioning
    counter = 0
    for row in range(2, height-4):
        for col in range(1, width-1):
            # if row is odd, setup the obstacle pegs
            if (row % 2 == 1):
                if (counter % 2 == 0):
                    if (col%2 == 0):
                        board[row][col] = BLACK
                else:
                    if (col%2 == 1):
                        board[row][col] = BLACK

        # obstacle offset
        if row % 2 == 1:
            counter += 1

    return board

In [44]:
def single_simulation(ball_col):
    fig = plt.figure()
    metadata = dict(title='Single Plinko drop animation', artist='Jeffrey Chen')
    writer = FFMpegWriter(fps=5, metadata=metadata)

    board = setup_board(height, width)
    ball_row = BALL_START_ROW

    if ball_col <= 0 or ball_col >= width-1:
        # if the user sets the ball_x start position out of bounds, change it
        ball_col = int(width / 2)

    # set the color of the ball
    board[ball_row][ball_col] = BALL_COLOR
    
    # use datetime to change random seed for ball drops
    time_int = int(datetime.datetime.now().strftime("%Y%m%d%H%M%S"))
    random.seed(time_int % 1201)
    
    # start grabbing frames
    with writer.saving(fig, "plinko_single.mp4", dpi=200):
        plt.imshow(board, interpolation='nearest', cmap='gray')
        plt.axis('off'); 
        plt.show()
        plt.draw()
        plt.pause(FRAME_PAUSE)
        writer.grab_frame()
        
        # simulate the ball falling through the board
        while ball_row < (height-2):
            # if the value below current row is 1 (free space), go straight down
            if np.array_equiv(board[ball_row+1][ball_col], WHITE):
                # set old value = old color
                if ball_row == BALL_START_ROW:
                    board[ball_row][ball_col] = GREEN
                else:
                    board[ball_row][ball_col] = WHITE        

            else:
                # otherwise, there is an obstacle and fall left or right
                board[ball_row][ball_col] = WHITE
                random_gen = random.random()

                if random_gen < 0.5:
                    # fall left or straight down
                    if ball_col > 1:
                        ball_col -= 1

                    else:
                        # ball is on the leftmost boundary, HAS to go right
                        ball_col += 1

                else:
                    # fall right
                    if ball_col < width - 2:
                        ball_col += 1

                    else:
                        # ball is on rightmost boundary, HAS to go left
                        ball_col -= 1

            # increment ball position and update color
            ball_row += 1
            board[ball_row][ball_col] = BALL_COLOR

            plt.imshow(board, interpolation='nearest', cmap='gray')
            plt.title("Plinko Simulated!")
            plt.axis('off'); 
            plt.show()
            plt.draw()
            plt.pause(FRAME_PAUSE)
            # grab frame and clear plot for fast performance
            writer.grab_frame()
            # if ball reached the end, do not clear frame to show final result
            if ball_row < height - 2:
                plt.clf()
        
# THE USER CAN CHANGE THIS VALUE, 1 <= ball_col starting position <= width-2     
start_pos = 7
single_simulation(start_pos)

In [ ]:
def simulate_distribution(ball_col, iterations):
    # keep track of how many balls landed in each column, to be displayed
    arr = [-1] * width
    
    # run through each iteration
    for iteration in range(iterations):
        # set a different seed for random number generation
        time_int = int(datetime.datetime.now().strftime("%Y%m%d%H%M%S"))
        random.seed(time_int + iteration)
        
        board = setup_board(height, width)
        ball_row = BALL_START_ROW

        if ball_col <= 0 or ball_col >= width-1:
            # if ball_col start position is out of bounds, place it in bounds
            ball_col = int(width / 2)

        # set the color of the ball
        board[ball_row][ball_col] = BALL_COLOR

        # simulate ball falling through
        while ball_row < (height-2):
            # if the value below me is 1 (free space), go straight down
            if np.array_equiv(board[ball_row+1][ball_col], WHITE):
                # set old value = old color
                if ball_row == BALL_START_ROW:
                    board[ball_row][ball_col] = GREEN
                else:
                    board[ball_row][ball_col] = WHITE        

            else:
                # otherwise, there is an obstacle and fall left or right
                board[ball_row][ball_col] = WHITE

                random_gen = random.uniform(0, 1)
                if random_gen < 0.5:
                    # fall left
                    if ball_col > 1:
                        ball_col -= 1

                    else:
                        # ball is on the leftmost boundary, HAS to go right
                        ball_col += 1

                else:
                    # fall right
                    if ball_col < width - 2:
                        ball_col += 1

                    else:
                        # ball is on rightmost boundary, HAS to go left
                        ball_col -= 1

            ball_row += 1
            board[ball_row][ball_col] = BALL_COLOR

        # grab ball_col
        arr[ball_col] += 1
        
    final_arr = []
    for x in arr:
        # if a ball dropped in this column, show it
        if x >= 0:
            final_arr.append(x)
            
    
    # plot final_arr
    x_axis = np.linspace(1, len(final_arr), len(final_arr))
    plt.clf()
    plt.bar(x_axis, final_arr)
    plt.title("Distribution of " + str(iterations) + " drops")
    plt.ylabel("Count")
    plt.xlabel("Landing Column")
    plt.show()
    
# USER CAN CHANGE ITERATIONS AND START_POS
iterations = 100000
# start the ball in the middle
start_pos = int(width / 2)
simulate_distribution(start_pos, iterations)